In [6]:
from datasets import load_dataset
import pandas as pd
import os
import yaml
import sys
sys.path.append("..")
from src.pred_plot import prep_data_pred_plot, data_split
%load_ext autoreload
%autoreload 2

token_file = open("../token_secret.yaml")
token_obj = yaml.load(token_file, Loader=yaml.FullLoader)
dataset = load_dataset("tappyness1/causion", use_auth_token=token_obj['TOKEN'])
counts_df = pd.DataFrame(dataset['train'])

Using custom data configuration tappyness1--causion-f0c7d8cb97d796fc
Found cached dataset parquet (C:/Users/neoce/.cache/huggingface/datasets/tappyness1___parquet/tappyness1--causion-f0c7d8cb97d796fc/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec)
100%|██████████| 1/1 [00:00<00:00, 144.77it/s]


In [5]:
counts_df.head()

date      time                                        view  car  \
0  2023-02-14  22:36:03               View_from_Second_Link_at_Tuas    0   
1  2023-02-14  22:36:03                   View_from_Tuas_Checkpoint    2   
2  2023-02-14  22:36:03  View_from_Woodlands_Causeway_Towards_Johor    2   
3  2023-02-14  22:36:03  View_from_Woodlands_Checkpoint_Towards_BKE    3   
4  2023-02-14  23:14:34               View_from_Second_Link_at_Tuas    0   

   motorcycle  large_vehicle  
0           0              1  
1           0              0  
2           0              0  
3           0              1  
4           0              6

In [23]:
from src.pred_plot import prep_data_pred_plot, data_split, train_model, predicted_figure, get_today, convert_date, gen_fig
from datetime import date, datetime, timedelta
from jupyter_dash import JupyterDash
import dash
from dash import Dash, html, dcc, Input, Output
final_table = prep_data_pred_plot(counts_df)
x_train, x_test, y_train, y_test = data_split(final_table)
clf = train_model(x_train, y_train)

g:\My Drive\DataScience\OMSA GaTech\08_CSE6242\Project\Org_Space\Causion\notebooks\..\src\pred_plot.py:117: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

g:\My Drive\DataScience\OMSA GaTech\08_CSE6242\Project\Org_Space\Causion\notebooks\..\src\pred_plot.py:118: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

g:\My Drive\DataScience\OMSA GaTech\08_CSE6242\Project\Org_Space\Causion\notebooks\..\src\pred_plot.py:120: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a fu

In [30]:
starter_variables = [x_train, str(date.today()), "07:00", "Tuas-Johor"]
figs = gen_fig()
fig = predicted_figure(clf, starter_variables, figs)
today = get_today()

In [33]:
app = JupyterDash(__name__)

app.title = 'CSE6242 Dashboard'
app.layout = html.Div([
    html.Div([
    dcc.DatePickerSingle(
    id='my_date_picker_single',
        min_date_allowed=date(2023, 4, 11),
        max_date_allowed=date(2024, 4, 11),
        initial_visible_month=date(today[0],today[1], today[2]),
        date=date(today[0],today[1], today[2])
    ),
    html.Div(id='output-container-date-picker-single')],
        style={'width':'20%','height':'0px', 'padding-left':'2%',
                                                 'display':'inline-block'}),
    html.Div([dcc.Dropdown(id='hours_dropdown_id',
                                     options=['00:00', '01:00', '02:00', '03:00', '04:00', '05:00', '06:00', '07:00', '08:00', '09:00', 
                         '10:00', '11:00', '12:00', '13:00', '14:00', '15:00', '16:00', '17:00', '18:00','19:00',
                         '20:00', '21:00', '22:00', '23:00'],
                                     value='07:00', clearable=False),html.Label("Estimated Leave Time")],
    style={'width':'20%','height':'60px', 'padding-left':'2%',
                                                 'display':'inline-block'}),
    html.Div([dcc.Dropdown(id='direction_id',
                                     options=['Johor-Tuas','Johor-Woodlands',
                                             'Tuas-Johor', 'Woodlands-Johor'],
                                     value="Tuas-Johor", clearable=False),html.Label("Direction")],
    style={'width':'20%','height':'60px', 'padding-left':'2%',
                                                 'display':'inline-block'}),
    html.Div(dcc.Graph(id='final_output', figure=fig))])


@app.callback(Output('output-container-date-picker-single', 'children'),
    Input('my_date_picker_single', 'date'))
def update_output(date_value):
    string_prefix = 'Travel Day: '
    if date_value is not None:
        date_object = date.fromisoformat(date_value)
        date_string = convert_date(date_value)
        return string_prefix + date_string
    
@app.callback(Output('final_output', "figure"),
              Input('my_date_picker_single', 'date'),
              Input('hours_dropdown_id', 'value'),
              Input('direction_id', 'value'))
def update_final_output_hour(my_date_picker_single, hours_dropdown_id, direction_id):
    starter_variables[0] = x_train
    starter_variables[1] = str(my_date_picker_single)
    starter_variables[2] = str(hours_dropdown_id)
    starter_variables[3] = str(direction_id)
    fig = predicted_figure(clf, starter_variables, figs)
    return fig

In [34]:
app.run_server(mode='inline')

Dash is running on http://127.0.0.1:8050/



In [2]:
from datetime import date

str(date.today())

'2023-04-14'